## Import libraries and set the environment

In [1]:
import pickle

with open('./token.pkl', 'rb') as f:
    token = pickle.load(f)

import os
os.environ["HF_HUB_DISABLE_SYMLINKS_WARNING"] = "1"
os.environ["CUDA_VISIBLE_DEVICES"] = "0"  # Select GPU 0 (or change the index as needed)

from huggingface_hub import login
login(token['hf_token'])

import torch
device = "cuda" if torch.cuda.is_available() else "mps" if torch.backends.mps.is_available() else "cpu"
print(f"Using {device}")

import tqdm

FileNotFoundError: [Errno 2] No such file or directory: './token.pkl'

## Convert mp4 to wav

In [ ]:
video_path = "E:/GAR/videos"
video_sub_path = {'R1': ["G4 R1 VOBS (1 day)"], 'R2': ["G4 R2 VOBS (2 days)/Day1", "G4 R2 VOBS (2 days)/Day2"], 'R3': ["G4 R3 VOBS (2 days)/Day1", "G4 R3 VOBS (2 days)/Day2"]}

# videos = os.listdir(os.path.join(video_path, 'G4 R1 VOBS (1 day)'))
# videos = [x for x in videos if x[-3:]=='mp4']

# os.makedirs(os.path.join(video_path, "wavs_R1_day1"), exist_ok=True)
# wav_path = os.path.join(video_path, "wavs_R1_day1")

# print(len(videos))

In [ ]:
# !pip uninstall moviepy
# !pip install moviepy==1.0.3

In [ ]:
# from moviepy.editor import VideoFileClip

# def video_to_wav(video_path, wav_path, video):
#     # Load the video file
#     video_clip = VideoFileClip(f"{video_path}/{video}")
    
#     # Extract the audio from the video
#     audio_clip = video_clip.audio
    
#     # Write the audio to a WAV file
#     audio_clip.write_audiofile(f"{wav_path}/{video[:-4]}.wav", codec='pcm_s16le', fps=audio_clip.fps)
    
#     # Close the video and audio clips to free up resources
#     audio_clip.close()
#     video_clip.close()


# for sub_path in list(video_sub_path.values()):
#     videos = os.listdir(os.path.join(video_path, sub_path))
#     wav_path = os.path.join(video_path, 'wavs_'+sub_path)
#     os.makedirs(wav_path, exist_ok=True)
    
#     print(sub_path, len(videos))
    
#     for video in tqdm.tqdm(videos):
#         if os.path.exists(os.path.join(video_path, 'wavs_'+sub_path, f"{video[:-4]}.wav")):
#             continue
#         video_to_wav(os.path.join(video_path, sub_path), wav_path, video)

## Functions to cut the wav file and make transcript

In [ ]:
import subprocess

def extract_audio_segment(input_file, start_time, duration, output_file):
    input_file = os.path.abspath(input_file)
    output_file = os.path.abspath(output_file)
    
    # Construct FFmpeg command
    command = [
        'ffmpeg',
        '-i', input_file,      # Input file
        '-ss', str(start_time), # Start time (e.g., "00:01:30")
        '-t', str(duration),    # Duration in seconds (e.g., 10)
        output_file            # Output file
    ]
    
    try:
        # Run the command and capture the error if any
        result = subprocess.run(command, check=True, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
        print()
        print(f"Extracted segment saved to {output_file}")
        print(result.stdout.decode())  # Print FFmpeg stdout
        
    except subprocess.CalledProcessError as e:
        print()
        print(f"Error: {e.stderr.decode()}")  # Print FFmpeg stderr if it fails

def transcript(audio, output_path, min_speakers=None, max_speakers=None, prt=False):

    if prt:
        print("1. Transcribe with original whisper (batched)")
    result = tsrc_model.transcribe(audio)

    result_df = pd.DataFrame(result['segments'])
    
    if not len(result_df):
        result_df = pd.DataFrame(columns=['start', 'end', 'text'])
        
    result_df = result_df[['start', 'end', 'text']]
    result_df['language'] = result['language']

    if prt:
        print(result_df)

    result_df.to_csv(output_path, index=False)

    print(f"{output_path} is saved.")# Time {time.time() - start_time: .5f}")

    return result_df

## Add transcript to the human coding dataframe

In [ ]:
import time
import whisper

tsrc_model = whisper.load_model("large-v3", device)

In [ ]:
import pandas as pd

pd.set_option("display.max_rows", None) 
pd.set_option("display.max_columns", None) 

# each csv file is extracted from "G4 final data.xlsx"
coding = {}
coding['R1'] = pd.read_csv("../G4_R1.csv")
coding['R2'] = pd.read_csv("../G4_R2.csv")
coding['R3'] = pd.read_csv("../G4_R3.csv")

coding['R1'].sort_values(by=['Video names', 'Obs. Entry'])
coding['R2'].sort_values(by=['Video names', 'Obs. Entry'])
coding['R3'].sort_values(by=['Video names', 'Obs. Entry'])

coding['R1']['tsrc'] = None
coding['R2']['tsrc'] = None
coding['R3']['tsrc'] = None

coding['R2'] = coding['R2'].dropna(subset=['Video names'])

In [8]:
from datetime import timedelta

for rnd in ['R1', 'R2', 'R3']:
    
    video_list = coding[rnd]['Video names'].unique()
    wav_not_exist = list()
    
    for video in video_list:
    
        found = False
        for sub_path in video_sub_path[rnd]:
        
            wav_path = os.path.join(video_path, 'wavs_' + sub_path)
            input_file = os.path.join(wav_path, f"{video}.wav")
            
            if os.path.exists(input_file):
                found = True

                chunk_path = os.path.join(video_path, 'chunks_' + sub_path)
                tsrc_dir = os.path.join(video_path, 'tsrc_' + sub_path)
    
                df = coding[rnd][coding[rnd]['Video names'] == video]
                times = list(df['Video minutes'].unique())
        
                for time in times:
                    df_time = df[df['Video minutes'] == time]
                    start_time = time.split('-')[0]
                    start_time_split = start_time.split(':')

                    if len(start_time_split) > 2:

                    else:
                        start_min, start_sec = map(int, start_time_split)
                        start_time = timedelta(minutes=start_min, seconds=start_sec)
        
                    for row_index in df_time.index:
                        _, start_min, start_sec = map(int, str(start_time).split(':'))
                        
                        # if os.path.exists(tsrc_file):
                        #     print(f"{tsrc_file} exists")
                        #     continue
        
                        if start_min == 0 and start_sec == 0:
                            extract_time = start_time
                            duration = 22
                        else:
                            extract_time = start_time - timedelta(seconds=2)
                            duration = 24

                        tsrc_file = os.path.join(tsrc_dir, f"{video}_{start_min:02}_{start_sec:02}_whisper.csv")
                        chunk_file = os.path.join(chunk_path, f"{video}_{start_min:02}_{start_sec:02}.wav")
                        extract_audio_segment(input_file, extract_time, duration, chunk_file)            
        
                        tsrc = transcript(chunk_file, tsrc_file, max_speakers=3)
        
                        merged_tsrc = ' '.join(tsrc['text'].astype(str)) if not tsrc.empty else None
                        coding[rnd].at[row_index, 'tsrc'] = merged_tsrc
        
                        start_time += timedelta(seconds=20)
    
            else:
                continue
    
        if not found:
            print(f"{video}.wav does not exist")
            wav_not_exist.append(input_file)


Extracted segment saved to E:\GAR\videos\chunks_G4 R1 VOBS (1 day)\G4 Online Archer City Amy Huseman_00_00.wav

E:/GAR/videos\tsrc_G4 R1 VOBS (1 day)\G4 Online Archer City Amy Huseman_00_00_whisper.csv is saved.

Extracted segment saved to E:\GAR\videos\chunks_G4 R1 VOBS (1 day)\G4 Online Archer City Amy Huseman_00_20.wav

E:/GAR/videos\tsrc_G4 R1 VOBS (1 day)\G4 Online Archer City Amy Huseman_00_20_whisper.csv is saved.

Extracted segment saved to E:\GAR\videos\chunks_G4 R1 VOBS (1 day)\G4 Online Archer City Amy Huseman_00_40.wav

E:/GAR/videos\tsrc_G4 R1 VOBS (1 day)\G4 Online Archer City Amy Huseman_00_40_whisper.csv is saved.

Extracted segment saved to E:\GAR\videos\chunks_G4 R1 VOBS (1 day)\G4 Online Archer City Amy Huseman_01_00.wav

E:/GAR/videos\tsrc_G4 R1 VOBS (1 day)\G4 Online Archer City Amy Huseman_01_00_whisper.csv is saved.

Extracted segment saved to E:\GAR\videos\chunks_G4 R1 VOBS (1 day)\G4 Online Archer City Amy Huseman_01_20.wav

E:/GAR/videos\tsrc_G4 R1 VOBS (1 da

ValueError: too many values to unpack (expected 2)

In [69]:
from datetime import timedelta

for rnd in ['R3']:
    
    video_list = coding[rnd]['Video names'].unique()
    wav_not_exist = list()
    
    for video in video_list:
    
        found = False
        for sub_path in video_sub_path[rnd]:
        
            wav_path = os.path.join(video_path, 'wavs_' + sub_path)
            input_file = os.path.join(wav_path, f"{video}.wav")
            
            if os.path.exists(input_file):
                found = True

                chunk_path = os.path.join(video_path, 'chunks_' + sub_path)
                tsrc_dir = os.path.join(video_path, 'tsrc_' + sub_path)
    
                df = coding[rnd][coding[rnd]['Video names'] == video]
                times = list(df['Video minutes'].unique())
        
                for time in times:
                    df_time = df[df['Video minutes'] == time]
                    start_time = time.split('-')[0]
                    start_time_split = start_time.split(':')
                    start_time_split = [int(t) for t in start_time_split]

                    if len(start_time_split) > 2:
                        start_min, start_sec = [start_time_split[0] * 60 + start_time_split[1], start_time_split[2]]
                        start_time = timedelta(minutes=start_min, seconds=start_sec)

                    else:
                        start_min, start_sec = map(int, start_time_split)
                        start_time = timedelta(minutes=start_min, seconds=start_sec)
        
                    for row_index in df_time.index:

                        _, start_min, start_sec = map(int, str(start_time).split(':'))
                        print(start_min, start_sec)

                        # if os.path.exists(tsrc_file):
                        #     print(f"{tsrc_file} exists")
                        #     continue

                        # if not coding[rnd].at[row_index, 'tsrc'] == None:
                        #     start_time += timedelta(seconds=20)
                        #     continue
        
                        if start_min == 0 and start_sec == 0:
                            extract_time = start_time
                            duration = 22
                        else:
                            extract_time = start_time - timedelta(seconds=2)
                            duration = 24
                        
                        tsrc_file = os.path.join(tsrc_dir, f"{video}_{start_min:02}_{start_sec:02}_whisper.csv")
                        chunk_file = os.path.join(chunk_path, f"{video}_{start_min:02}_{start_sec:02}.wav")
                        extract_audio_segment(input_file, extract_time, duration, chunk_file)            
        
                        tsrc = transcript(chunk_file, tsrc_file, max_speakers=3)
        
                        merged_tsrc = ' '.join(tsrc['text'].astype(str)) if not tsrc.empty else None
                        coding[rnd].at[row_index, 'tsrc'] = merged_tsrc
        
                        start_time += timedelta(seconds=20)
    
            else:
                continue
    
        if not found:
            print(f"{video}.wav does not exist")
            wav_not_exist.append(input_file)

5 0

Extracted segment saved to E:\GAR\videos\chunks_G4 R3 VOBS (2 days)\Day2\G4 Online Agua Dulce Sonia Almeida Week 9 Day 2_05_00.wav

E:/GAR/videos\tsrc_G4 R3 VOBS (2 days)/Day2\G4 Online Agua Dulce Sonia Almeida Week 9 Day 2_05_00_whisper.csv is saved.
5 20

Extracted segment saved to E:\GAR\videos\chunks_G4 R3 VOBS (2 days)\Day2\G4 Online Agua Dulce Sonia Almeida Week 9 Day 2_05_20.wav

E:/GAR/videos\tsrc_G4 R3 VOBS (2 days)/Day2\G4 Online Agua Dulce Sonia Almeida Week 9 Day 2_05_20_whisper.csv is saved.
5 40

Extracted segment saved to E:\GAR\videos\chunks_G4 R3 VOBS (2 days)\Day2\G4 Online Agua Dulce Sonia Almeida Week 9 Day 2_05_40.wav

E:/GAR/videos\tsrc_G4 R3 VOBS (2 days)/Day2\G4 Online Agua Dulce Sonia Almeida Week 9 Day 2_05_40_whisper.csv is saved.
6 0

Extracted segment saved to E:\GAR\videos\chunks_G4 R3 VOBS (2 days)\Day2\G4 Online Agua Dulce Sonia Almeida Week 9 Day 2_06_00.wav

E:/GAR/videos\tsrc_G4 R3 VOBS (2 days)/Day2\G4 Online Agua Dulce Sonia Almeida Week 9 Day 

#### Files to check

G4 F2F Buffalo Tonya Barrentine Week 9 Day 2_05_00_whisper --- one more line?

G4 F2F Groveton Johnnie Holley Week 9 Day 2.wav does not exist  
G4 F2F Driscoll Jessica Contreras Week 9 Day 2.wav does not exist  
G4 F2F Buffalo Tonya Barrentine Week 9 Day 2.wav does not exist  
G4 F2F Rising Star Elizabeth Sanchez Week 9 Day 2.wav does not exist  
G4 Online Laneville Jimmie Zotz Week 9 Day 2 Mentoring.wav does not exist  
G4 F2F Fort Hancock Francisco Retamoza W9D2 2of2.wav does not exist  

In [73]:
coding['R3']

School ID   Teacher ID  Condition  \
0                   Agua Dulce Elementary  V4-22010111          1   
1                   Agua Dulce Elementary  V4-22010111          1   
2                   Agua Dulce Elementary  V4-22010111          1   
3                   Agua Dulce Elementary  V4-22010111          1   
4                   Agua Dulce Elementary  V4-22010111          1   
5                   Agua Dulce Elementary  V4-22010111          1   
6                   Agua Dulce Elementary  V4-22010111          1   
7                   Agua Dulce Elementary  V4-22010111          1   
8                   Agua Dulce Elementary  V4-22010111          1   
9                   Agua Dulce Elementary  V4-22010111          1   
10                  Agua Dulce Elementary  V4-22010111          1   
11                  Agua Dulce Elementary  V4-22010111          1   
12                  Agua Dulce Elementary  V4-22010111          1   
13                  Agua Dulce Elementary  V4-22010111          1   
14                  Agua Dulce Elementary  V4-22010111          1   
15                  Agua Dulce Elementary  V4-22010111          1   
16                  Agua Dulce Elementary  V4-22010111          1   
17                  Agua Dulce Elementary  V4-22010111          1   
18                  Agua Dulce Elementary  V4-22010111          1   
19                  Agua Dulce Elementary  V4-22010111          1   
20                  Agua Dulce Elementary  V4-22010111          1   
21                  Agua Dulce Elementary  V4-22010111          1   
22                  Agua Dulce Elementary  V4-22010111          1   
23                  Agua Dulce Elementary  V4-22010111          1   
24                  Agua Dulce Elementary  V4-22010111          1   
25                  Agua Dulce Elementary  V4-22010111          1   
26                  Agua Dulce Elementary  V4-22010111          1   
27                  Agua Dulce Elementary  V4-22010111          1   
28                  Agua Dulce Elementary  V4-22010111          1   
29                  Agua Dulce Elementary  V4-22010111          1   
30                  Agua Dulce Elementary  V4-22010111          1   
31                  Agua Dulce Elementary  V4-22010111          1   
32                  Agua Dulce Elementary  V4-22010111          1   
33                  Agua Dulce Elementary  V4-22010111          1   
34                  Agua Dulce Elementary  V4-22010111          1   
35                  Agua Dulce Elementary  V4-22010111          1   
36                  Agua Dulce Elementary  V4-22010111          1   
37                  Agua Dulce Elementary  V4-22010111          1   
38                  Agua Dulce Elementary  V4-22010111          1   
39                  Agua Dulce Elementary  V4-22010111          1   
40                  Agua Dulce Elementary  V4-22010111          1   
41                  Agua Dulce Elementary  V4-22010111          1   
42                  Agua Dulce Elementary  V4-22010111          1   
43                  Agua Dulce Elementary  V4-22010111          1   
44                  Agua Dulce Elementary  V4-22010111          1   
45                  Agua Dulce Elementary  V4-22010111          1   
46                  Agua Dulce Elementary  V4-22010111          1   
47                  Agua Dulce Elementary  V4-22010111          1   
48                  Agua Dulce Elementary  V4-22010111          1   
49                  Agua Dulce Elementary  V4-22010111          1   
50                  Agua Dulce Elementary  V4-22010111          1   
51                  Agua Dulce Elementary  V4-22010111          1   
52                  Agua Dulce Elementary  V4-22010111          1   
53                  Agua Dulce Elementary  V4-22010111          1   
54                  Agua Dulce Elementary  V4-22010111          1   
55                  Agua Dulce Elementary  V4-22010111          1   
56                  Agua Dulce Elementary  V4-22010111          1   
57                  Agua Dulce

In [71]:
wav_not_exist

[]

In [72]:
# coding['R1'].to_csv(os.path.join(video_path, "G4_R1_tsrc_whisper.csv"))
# coding['R2'].to_csv(os.path.join(video_path, "G4_R2_tsrc_whisper.csv"))
coding['R3'].to_csv(os.path.join(video_path, "G4_R3_tsrc_whisper.csv"))

In [ ]:
# # R1
# from datetime import timedelta

# video_list = list(coding['R1']['Video names'].unique())

# os.makedirs(os.path.join(video_path, "chunk_R1_day1"), exist_ok=True)
# os.makedirs(os.path.join(video_path, "tsrc_R1_day1"), exist_ok=True)
# chunk_path = os.path.join(video_path, "chunk_R1_day1") 
# tsrc_dir = os.path.join(video_path, "tsrc_R1_day1")

# # loop on videos
# for video in video_list:
#     input_file = os.path.join(wav_path, f"{video}.wav")
    
#     df = coding['R1'][coding['R1']['Video names'] == video]
#     times = list(df['Video minutes'].unique())

#     # loop on 5-minute video chunk
#     for time in times:
#         df_time = df[df['Video minutes'] == time]
#         start_time = time.split('-')[0]
#         start_min, start_sec = map(int, start_time.split(':'))

#         start_time = timedelta(minutes=start_min, seconds=start_sec)
        
#         # loop on 20-second row
#         for row_index in df_time.index:

#             _, start_min, start_sec = map(int, str(start_time).split(':'))

#             if (int(start_min) == 0) & (int(start_sec) == 0):
#                 extract_time = start_time
#                 duration = 22

#             else:
#                 extract_time = start_time - timedelta(seconds=2)
#                 duration = 24
                
#             chunk_file = os.path.join(chunk_path, \
#                                       f"{video}_{start_min:02}_{start_sec:02}.wav")
#             # print('----', row, extract_time)
#             extract_audio_segment(input_file, extract_time, duration, chunk_file)            

#             tsrc_file = os.path.join(tsrc_dir, f"{video}_{start_min:02}_{start_sec:02}.csv")
#             tsrc = transcript(chunk_file, tsrc_file, max_speakers=3)

#             if tsrc.shape[0] == 0:
#                 merged_tsrc = None

#             else:
#                 merged_tsrc = ' '.join(tsrc['text'].astype(str))

#             coding['R1'].at[row_index, 'tsrc'] = merged_tsrc

#             start_time += timedelta(seconds=20)
#     #         break
#     #     break
#     # break